In [10]:
from math import log 
import numpy as np
from loadMnist import load_images, load_labels

In [2]:
# 讀資料
train_data  = load_images("data/train-images.idx3-ubyte")
train_label = load_labels("data/train-labels.idx1-ubyte")
test_data   = load_images("data/t10k-images.idx3-ubyte")
test_label  = load_labels("data/t10k-labels.idx1-ubyte")

In [3]:
# 目標: 紀錄各label機率(P(0),P(1),....)
# 1.創一個字典，紀錄各label數量
label_number_dict = {}
for label in train_label:
    if label in label_number_dict:
        label_number_dict[label] += 1
    else:
        label_number_dict[label] = 1
print("label_number_dict: ", label_number_dict)


# 2. 創一個字典，紀錄各label機率(P(0),P(1),....)
label_probability_dict = {}
for label in label_number_dict:
    label_probability_dict[label] = label_number_dict[label] / 60000
print("label_probability_dict: ", label_probability_dict)

label_number_dict:  {5: 5421, 0: 5923, 4: 5842, 1: 6742, 9: 5949, 2: 5958, 3: 6131, 6: 5918, 7: 6265, 8: 5851}
label_probability_dict:  {5: 0.09035, 0: 0.09871666666666666, 4: 0.09736666666666667, 1: 0.11236666666666667, 9: 0.09915, 2: 0.0993, 3: 0.10218333333333333, 6: 0.09863333333333334, 7: 0.10441666666666667, 8: 0.09751666666666667}


In [4]:
def gussian(pixel_range, mean, var):
    p = 1 / (np.sqrt(2 * np.pi * var)) * np.exp(-(pixel_range - mean) ** 2 / (2 * var))
    return p

In [67]:
# 目標: 使用高斯機率，算各別pixel條件機率，例:P(第一格,暗淡=25|label=0)=0.05,P(第一格,暗淡=85|label=0)=0.05,...,P(第七八四格, 暗淡=255|lebel=9)=0.01
# 1.創一個三維 數量 矩陣儲存結果[10*784*256]，先計算train data每一個pixel的mean&var
condiction_probability3D = np.zeros((10,784,256))
for label in range(10):
    temp = train_data[train_label==label]  # 挑出各別label資料算各pixel mean&var
    mean = np.mean(temp, axis=0)
    var  = np.var(temp, axis=0)
    var[var==0] = 10  # TODO=?????                 # var有0，在計算高斯機率時會divide by zero，所以假設一個很接近0的值?????
    for i in range(784):
        for pixel_range in range(256):
            condiction_probability3D[label][i][pixel_range] = gussian(pixel_range, mean[i], var[i])   # 高斯機率算每個pixel機率


In [69]:
# 進行test資料集，離散版本運算
error = 0
for j in range(len(test_data)): 
    prob_sum = 0
    prob_logs = []
    for label in range(10):
        prob_log = 0
        for i, pixel in enumerate(test_data[j]):  
            pixel_range = pixel
            prob_log += log(max(1e-125, condiction_probability3D[label][i][pixel_range]))  # log x越接近0,y越接近負無限大,又因為log0不存在，所以將機率0設定一個非常接近零的數值當屏障 

        prob_logs.append(prob_log + log(label_probability_dict[label]))  # 最後要乘P(label)的機率
        prob_sum += prob_log + log(label_probability_dict[label])
    
    # 印出結果 #
    print("Postirior (in log scale):")
    log_result = np.array(prob_logs)/prob_sum
    for i, v in enumerate(log_result):
        print("{}: {}".format(i, v))
    pred = np.argmin(log_result)         # 因為開log，所以要選最小的才是機率最高的
    ans  = test_label[j] 
    print("Prediction: {}, Ans: {}".format(pred, ans))
    print()
    if pred != ans:
        error += 1
    
# 計算錯誤率 #
error_rate = error/len(test_data)
print("Error rate: {}".format(error_rate))

Postirior (in log scale):
0: 0.10272874528972735
1: 0.12981384607783447
2: 0.10665689756495852
3: 0.09429411449702331
4: 0.09365178949549509
5: 0.09636084102228601
6: 0.11587821038770016
7: 0.08170174758711524
8: 0.09428808481754963
9: 0.08462572326031019
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.08993978445356625
1: 0.11538205198163078
2: 0.07338187005636514
3: 0.08591061708759624
4: 0.1090290617679038
5: 0.09234624210542848
6: 0.08424086671239761
7: 0.13456786843690516
8: 0.09521386340086685
9: 0.11998777399733965
Prediction: 2, Ans: 2

Postirior (in log scale):
0: 0.10989112787560373
1: 0.07601724316515235
2: 0.10298305210836327
3: 0.10069063613256718
4: 0.10112716663036743
5: 0.10183646398548032
6: 0.09991786981305055
7: 0.1069522664385538
8: 0.09935036808932222
9: 0.10123380576153905
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.08040099914608834
1: 0.18023660605585257
2: 0.0908753591979088
3: 0.08915596638641256
4: 0.09283486863421185
5: 0.08884050568103098
6:

Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.11366298466695658
1: 0.07703561118568591
2: 0.10562001994638695
3: 0.10040353470741667
4: 0.10126570372907163
5: 0.10140582656577656
6: 0.10369004579394393
7: 0.10115359832781462
8: 0.09896701556512633
9: 0.09679565951182076
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.09373162676246997
1: 0.10692864321623992
2: 0.09468290281275472
3: 0.09245854406442262
4: 0.10185660703446749
5: 0.09455319133706898
6: 0.09820313261853068
7: 0.11520886952158371
8: 0.09345031042130869
9: 0.10892617221115317
Prediction: 3, Ans: 2

Postirior (in log scale):
0: 0.1136519189578265
1: 0.075352974359853
2: 0.1029885255222477
3: 0.09945321980783926
4: 0.10254598181760168
5: 0.10062323901986109
6: 0.09883228640219285
7: 0.11065856430538912
8: 0.09729090847430887
9: 0.09860238133287998
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.10794745799610687
1: 0.07755356347256102
2: 0.10455387205324584
3: 0.10134897911453342
4: 0.10228696082966075
5: 

9: 0.08607000395038494
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.09807769299802874
1: 0.09840384954404852
2: 0.09887534209040955
3: 0.09178594582830304
4: 0.10157720554024509
5: 0.09505309883569824
6: 0.10392510932436341
7: 0.11534953300354321
8: 0.0935629296759048
9: 0.10338929315945537
Prediction: 3, Ans: 3

Postirior (in log scale):
0: 0.09692324481417086
1: 0.13051968658870053
2: 0.09293355617193558
3: 0.10184887284799972
4: 0.0945121751325623
5: 0.09514230241488036
6: 0.09965946002129894
7: 0.1016009020346172
8: 0.09506205335219545
9: 0.0917977466216393
Prediction: 9, Ans: 2

Postirior (in log scale):
0: 0.11629230653485768
1: 0.09210039275168172
2: 0.11012997075858041
3: 0.09594152054242638
4: 0.0955926922966868
5: 0.09692309572581012
6: 0.1156407204144042
7: 0.09408599188027557
8: 0.09360503620812138
9: 0.08968827288715585
Prediction: 9, Ans: 9

Postirior (in log scale):
0: 0.09994719979508734
1: 0.15714116787081328
2: 0.10403442763912037
3: 0.09256938060071986
4: 0.

Postirior (in log scale):
0: 0.10333848265302294
1: 0.08852996340945579
2: 0.10523225841233944
3: 0.09513067294694409
4: 0.09939241864123032
5: 0.09759347915217204
6: 0.10995552980529609
7: 0.10540837476345517
8: 0.09587531231893591
9: 0.09954350789714826
Prediction: 1, Ans: 3

Postirior (in log scale):
0: 0.11265632988985252
1: 0.12351161425675858
2: 0.10612610546834823
3: 0.09817282162268715
4: 0.09106598210174123
5: 0.09713070266178217
6: 0.1077221967871574
7: 0.08596360884500531
8: 0.09567116927056464
9: 0.08197946909610275
Prediction: 9, Ans: 9

Postirior (in log scale):
0: 0.11291648559449208
1: 0.1052303208996312
2: 0.10346786633176579
3: 0.09874833187956361
4: 0.09590033541164014
5: 0.09911195178799809
6: 0.10360627379747074
7: 0.09316083851907425
8: 0.09592728068527057
9: 0.0919303150930935
Prediction: 9, Ans: 7

Postirior (in log scale):
0: 0.10690286473696585
1: 0.10104066661984189
2: 0.1017249211563407
3: 0.09930807006724279
4: 0.09681114039214583
5: 0.09929358140354132
6: 

Postirior (in log scale):
0: 0.1049632206502071
1: 0.12184916454943064
2: 0.10043052216689434
3: 0.09581667059041848
4: 0.0924679538622065
5: 0.0941240148188298
6: 0.11226165564350099
7: 0.09903566858539858
8: 0.0889533730536503
9: 0.09009775607946323
Prediction: 8, Ans: 8

Postirior (in log scale):
0: 0.08093355626974805
1: 0.1505482960342147
2: 0.07074487090021138
3: 0.07849685124153476
4: 0.09961111423096923
5: 0.0821070913113063
6: 0.0886362353498821
7: 0.1353784752689315
8: 0.0916374294700593
9: 0.1219060799231428
Prediction: 2, Ans: 2

Postirior (in log scale):
0: 0.08735908527584992
1: 0.1459610608617613
2: 0.0951502666453287
3: 0.09162473128779057
4: 0.09503137712684546
5: 0.09268749661010256
6: 0.09208197208014939
7: 0.11197771129764865
8: 0.09074299819738425
9: 0.0973833006171391
Prediction: 0, Ans: 0

Postirior (in log scale):
0: 0.10270570241912806
1: 0.12654956138726892
2: 0.09051502369804026
3: 0.09722129449514157
4: 0.09635557726735948
5: 0.09450322319035737
6: 0.0942983

...

Postirior (in log scale):
0: 0.11629678302752017
1: 0.0755068942082563
2: 0.1030166317217853
3: 0.09980270056476452
4: 0.09974078011733428
5: 0.10109651745081882
6: 0.10750076214590613
7: 0.1029808616318864
8: 0.09686586529235014
9: 0.09719220383937782
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.10694782647238263
1: 0.09987770748824792
2: 0.10793172761994532
3: 0.0994919758100854
4: 0.0986658776199479
5: 0.1003540309846006
6: 0.10993262162774683
7: 0.08911459468126857
8: 0.0986196769993627
9: 0.08906396069641219
Prediction: 9, Ans: 7

Postirior (in log scale):
0: 0.11404570646725984
1: 0.07516572205599804
2: 0.10392532116468248
3: 0.09896401258105017
4: 0.09959076737270557
5: 0.1003110449551065
6: 0.11248036148208888
7: 0.10238387798806745
8: 0.0965614494122907
9: 0.09657173652075024
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.10554321929290715
1: 0.10196195436479288
2: 0.11009659189929012
3: 0.09613735360214239
4: 0.09592486882378895
5: 0.09660433712068735
6: 0.119

Postirior (in log scale):
0: 0.10492772840983154
1: 0.11958134692625753
2: 0.1078050984592423
3: 0.0988635322915622
4: 0.09397365788626616
5: 0.09731186202076006
6: 0.11384320033548168
7: 0.08378158569695497
8: 0.09492277429476127
9: 0.08498921367888218
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.09605759277189949
1: 0.08204196671631225
2: 0.1031440831715592
3: 0.09525350718061348
4: 0.09692628223905252
5: 0.09277222504682132
6: 0.12253103547200678
7: 0.1144258514812069
8: 0.09063720073818175
9: 0.10621025518234636
Prediction: 1, Ans: 5

Postirior (in log scale):
0: 0.09868205110704831
1: 0.13540572565308387
2: 0.09626523076892868
3: 0.10010336988921481
4: 0.08805597395009361
5: 0.09359582336695661
6: 0.09389323852689266
7: 0.10463713820839356
8: 0.0920663295996065
9: 0.09729511892978146
Prediction: 4, Ans: 4

Postirior (in log scale):
0: 0.08524538227199316
1: 0.1278944504856994
2: 0.08813897661826857
3: 0.08101644274950398
4: 0.10653056850092046
5: 0.0859457016866666
6: 0.0

Postirior (in log scale):
0: 0.10042944118204797
1: 0.10748894993226515
2: 0.09759559765932749
3: 0.10099445640557317
4: 0.09254647246135018
5: 0.09655215937765281
6: 0.1008328247607638
7: 0.10865020711110131
8: 0.0940143147527006
9: 0.1008955763572173
Prediction: 4, Ans: 4

Postirior (in log scale):
0: 0.09650909838927606
1: 0.10170472705623912
2: 0.1024923437506223
3: 0.10260657692241414
4: 0.09712338781521887
5: 0.09193643448092033
6: 0.10503889485556565
7: 0.1061503678521774
8: 0.09082271806308852
9: 0.10561545081447764
Prediction: 8, Ans: 5

Postirior (in log scale):
0: 0.09791925394494062
1: 0.12299283414053608
2: 0.09526590095724564
3: 0.09866560629693423
4: 0.09777787256445407
5: 0.09509963657204282
6: 0.08129539377774224
7: 0.1119736887601747
8: 0.09604105157731137
9: 0.10296876140861819
Prediction: 6, Ans: 6

Postirior (in log scale):
0: 0.10024262914166811
1: 0.13850407198819645
2: 0.1077436247776675
3: 0.09574476486709657
4: 0.09234312308185198
5: 0.09426009996463953
6: 0.1


Postirior (in log scale):
0: 0.1101716320242471
1: 0.07509105352458484
2: 0.10391297769204978
3: 0.09819528042089029
4: 0.10140704000910637
5: 0.09961799093381617
6: 0.11444528861968942
7: 0.1034184722006165
8: 0.09607429047798619
9: 0.09766597409701343
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.08538471265209702
1: 0.16794159899588856
2: 0.08978056878527897
3: 0.09350794915787117
4: 0.08546788311002881
5: 0.08835021584280589
6: 0.0844617932135581
7: 0.10987493232900042
8: 0.09271310496061125
9: 0.10251724095285977
Prediction: 6, Ans: 4

Postirior (in log scale):
0: 0.06945511203245316
1: 0.14551725656269968
2: 0.08928462650762492
3: 0.09353178843467544
4: 0.09997067929562511
5: 0.08341165869753388
6: 0.10564402951167678
7: 0.11350624598144012
8: 0.08552542353559055
9: 0.11415317944068032
Prediction: 0, Ans: 0

Postirior (in log scale):
0: 0.08814834507621344
1: 0.1623346128135686
2: 0.08665418540096909
3: 0.09446421616646536
4: 0.09492727255560347
5: 0.09328634690648722
6:

Postirior (in log scale):
0: 0.10930195516023095
1: 0.07647995984380274
2: 0.09804469086295868
3: 0.0934197873630218
4: 0.10812559022988794
5: 0.09650778779031179
6: 0.11191406407410523
7: 0.10461250600827227
8: 0.09287620722970728
9: 0.10871745143770137
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.09679348538297299
1: 0.14846162473228694
2: 0.10648461054970366
3: 0.09710872201735186
4: 0.09146596051799506
5: 0.09476391191254126
6: 0.10880934273418928
7: 0.0812773027212202
8: 0.0926890775252653
9: 0.08214596190647355
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.08192892641357434
1: 0.18045152197531225
2: 0.07826060567949035
3: 0.07626286828556979
4: 0.09616321803623992
5: 0.08181491491304946
6: 0.1135971502751582
7: 0.10282158539612435
8: 0.07621477821322145
9: 0.11248443081225987
Prediction: 8, Ans: 2

Postirior (in log scale):
0: 0.09648639067761776
1: 0.11509957196909223
2: 0.09283535177079184
3: 0.09667400354625075
4: 0.10196757717289504
5: 0.09345119254524303
6: 

In [70]:
print("Imagination of numbers in Bayesian classifier: ")
for label in range(10):
    temp = []
    for pixels in condiction_probability3D[label]:
        max_pixel_range_index = np.argmax(pixels)  # 選出淡到黑機率最大的pixel_range index
        if max_pixel_range_index >= 128:            # 因為>=128是1(黑) 
            temp.append(1)
        else:
            temp.append(0)
    
    # 印出數字 #
    print("{}:".format(label))
    for i in range(len(temp)):
        if i != 0 and i % 28 == 0:
            print()
        print(temp[i], end="")
    print()

Imagination of numbers in Bayesian classifier: 
0:
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000001110000000000
0000000000000111111100000000
0000000000001111111110000000
0000000000011111111110000000
0000000000111110001111000000
0000000001111000000111000000
0000000001110000000011100000
0000000011100000000011100000
0000000111100000000011100000
0000000111000000000011100000
0000000111000000000011000000
0000001110000000000111000000
0000001110000000000110000000
0000001110000000001110000000
0000001111000000111100000000
0000000111110011111000000000
0000000111111111110000000000
0000000011111111000000000000
0000000000111100000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
1:
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
000000000000000000